# Combine monthly and annual runoff and other information into merged per-glacier data-files for every basin

- The annual or monthly glacier runoff that is computed here is the sum of annual melt and liquid precipitation on and off the glacier using a fixed-gauge with a glacier minimum reference area from year 2000.

- Attention, no filling is done, those glaciers that did not run have np.NaN values
- two options:
    - `gcm_from_2000` : gcm directly from 2000 (results in differences between GCMs from 2000-2019) 
    - `w5e5_gcm_merged` : W5E5 from 2000-2019 and GCM from 2020 runoff

(the data got updated in March 2025, because some basins were accidentally missing)

In [1]:
import xarray as xr
import numpy as np
import pandas as pd
from time import gmtime, strftime
import oggm.cfg
from oggm import  utils, workflow, tasks, graphics
import json
import geopandas as gpd

# let's also do some visualisations ...
import matplotlib.pyplot as plt
import seaborn as sns

gcms_cmip6 = pd.read_csv('/home/www/oggm/cmip6/all_gcm_list.csv', index_col=0)   
all_GCM = gcms_cmip6.gcm.unique()
all_scenario = gcms_cmip6.ssp.unique()

# get the dataset where coordinates of glaciers are stored
frgi = utils.file_downloader('https://cluster.klima.uni-bremen.de/~oggm/rgi/rgi62_stats.h5')
#frgi = '/home/users/lschuster/glacierMIP/rgi62_stats.h5'
odf = pd.read_hdf(frgi, index_col=0)

# get the RGI ids of the glaciers of the chosen basin
pd_basin_num = gpd.read_file('/home/www/fmaussion/misc/magicc/basins_shape/glacier_basins.shp')

In [2]:
### all available gcm_scenario combinations ... 
len(gcms_cmip6)/2

73.0

In [3]:
pd_basin_num
# we will name them after their MRBID number
# here you can also get the initial glacierized area by dividing RGI_AREA through AREA_CALC

MRBID                                        RIVER_BASI CONTINENT  \
0    2103                                         INDIGIRKA      Asia   
1    2108                                                OB      Asia   
2    2302                                       BRAHMAPUTRA      Asia   
3    2306                                            GANGES      Asia   
4    2309                                             INDUS      Asia   
..    ...                                               ...       ...   
70   6241                                                PO    Europe   
71   6242                                             RHINE    Europe   
72   6243                                             RHONE    Europe   
73   6254                                           THJORSA    Europe   
74   6255  TORNEALVEN (also TORNIONJOKI, also TORNIONVAYLA)    Europe   

             OCEAN                SEA  AREA_CALC  Shape_Leng  Shape_Area  \
0     Arctic Ocean  East Siberian Sea   341234.0   85.604051   70.212499   
1     Arctic Ocean           Kara Sea  3040606.1  168.355250  448.342075   
2     Indian Ocean      Bay of Bengal   540782.5   66.054440   49.686611   
3     Indian Ocean      Bay of Bengal  1006558.6  122.349983   90.946880   
4     Indian Ocean        Arabian Sea   865012.6   81.286291   82.852275   
..             ...                ...        ...         ...         ...   
70  Atlantic Ocean       Adriatic Sea    73289.5   21.576098    8.425867   
71  Atlantic Ocean          North Sea   163122.3   48.247612   20.200160   
72  Atlantic Ocean  Mediterranean Sea    96637.6   28.004916   11.197342   
73  Atlantic Ocean     North Atlantic     8277.8    9.270847    1.545336   
74  Atlantic Ocean         Baltic Sea    40545.2   28.919025    8.685652   

     RGI_AREA                                           geometry  
0     171.941  POLYGON ((151.725 70.975, 151.725 70.97083, 15...  
1     763.493  POLYGON ((91.75 57.70417, 91.74542 57.70299, 9...  
2   10528.496  POLYGON ((97.76667 28.77083, 97.76335 28.77168...  
3    7906.081  MULTIPOLYGON (((88.02555 21.5715, 88.02361 21....  
4   27206.546  MULTIPOLYGON (((67.44167 23.97006, 67.44028 23...  
..        ...                                                ...  
70    313.417  POLYGON ((9.68333 46.425, 9.68418 46.42168, 9....  
71    336.922  POLYGON ((4.45638 52.14527, 4.46175 52.1411, 4...  
72    917.302  POLYGON ((6.84167 47.82083, 6.84167 47.81667, ...  
73    972.419  POLYGON ((-17.5 64.625, -17.50035 64.60591, -1...  
74     34.257  POLYGON ((23.69167 68.84167, 23.70214 68.84102...  

[75 rows x 10 columns]

check how many glaciers there are for an example basin:

In [4]:
basin = 'RHONE' #'RHONE' # INDUS
basin_idx = pd_basin_num[pd_basin_num['RIVER_BASI'] == basin]['MRBID'].values[0]
f = open('/home/www/fmaussion/misc/magicc/rgi_ids_per_basin.json')
rgis_basin = json.load(f)[str(basin_idx)]
odf_basin = odf.loc[rgis_basin]
print(basin, f', MRBID: {basin_idx},', f'n={len(rgis_basin)}')


RHONE , MRBID: 6243, n=1169


In [5]:
# choose only relevant variables for the basin aggregation 
variables = ['volume','area', 
             'melt_off_glacier', 'melt_on_glacier', 'liq_prcp_off_glacier', 'liq_prcp_on_glacier',
             'melt_off_glacier_monthly', 'melt_on_glacier_monthly', 'liq_prcp_off_glacier_monthly', 'liq_prcp_on_glacier_monthly']

In [12]:
creation_date = strftime("%Y-%m-%d %H:%M:%S", gmtime())  # here add the current time for info

bc = '_bc_2000_2019' # '_bc_1979_2014'
end_yr = '2100'  # you could change that to '2300'
cmip = 'CMIP6'  # or change that to CMIP5

path = f'/home/www/oggm/oggm-standard-projections/oggm_v16/2023.3/{cmip}/{end_yr}' 

merge = True #True
if merge:
    utils.mkdir(f'{path}/basins')
    for basin in pd_basin_num.RIVER_BASI: 
        # get the RGI ids of the glaciers of the chosen basin
        pd_basin_num = gpd.read_file('/home/www/fmaussion/misc/magicc/basins_shape/glacier_basins.shp')
        basin_idx = pd_basin_num[pd_basin_num['RIVER_BASI'] == basin]['MRBID'].values[0]

        print(basin_idx)
        
        area_basin_total = pd_basin_num[pd_basin_num['RIVER_BASI'] == basin]['AREA_CALC'].values[0]
        area_basin_glacier = pd_basin_num[pd_basin_num['RIVER_BASI'] == basin]['RGI_AREA'].values[0]
        f = open('/home/www/fmaussion/misc/magicc/rgi_ids_per_basin.json')
        rgis_basin = json.load(f)[str(basin_idx)]
        odf_basin = odf.loc[rgis_basin]
        utils.mkdir(f'{path}/basins/{basin_idx}')

        for hist in ['gcm_from_2000', 'w5e5_gcm_merged']:
            for GCM in ['CESM2-WACCM','CESM2','EC-Earth3', 'EC-Earth3-Veg']: #all_GCM:  # loop through all GCMs
                for scen in all_scenario:  # loop through all SSPs
                    try:  # check if GCM, SCENARIO combination exists
                        rid = '_{}_{}'.format(GCM, scen)  # put together the same filesuffix which was used during the projection runs
                        ds_all= []
                        for rgi_reg in odf_basin.O1Region.unique():
                            odf_basin_reg = odf_basin.loc[odf_basin.O1Region==rgi_reg]
                            rgis_basin_rgi_reg = odf_basin_reg.index.values
                            with xr.open_mfdataset(f'{path}/RGI{rgi_reg}/run_hydro_{hist}_{GCM}_{scen}{bc}_Batch*.nc') as ds_tmp:
                                ds_tmp = ds_tmp[variables]
                                ds_tmp = ds_tmp.sel(rgi_id=rgis_basin_rgi_reg).load()
                                ds_tmp['runoff_monthly'] = (ds_tmp['melt_off_glacier_monthly'] + ds_tmp['melt_on_glacier_monthly']
                                                            + ds_tmp['liq_prcp_off_glacier_monthly'] + ds_tmp['liq_prcp_on_glacier_monthly'])
                                ds_tmp['runoff'] = (ds_tmp['melt_off_glacier'] + ds_tmp['melt_on_glacier']
                                                            + ds_tmp['liq_prcp_off_glacier'] + ds_tmp['liq_prcp_on_glacier'])
                                # for the moment, only save these variables ...
                                ds_tmp = ds_tmp[['runoff', 'runoff_monthly', 'volume', 'area']]
                            ds_tmp.coords['gcm'] = GCM  # add GCM as a coordinate
                            ds_tmp.coords['gcm'].attrs['description'] = 'used global circulation model'  # add a description for GCM
                            ds_tmp = ds_tmp.expand_dims("gcm")  # add GCM as a dimension to all Data variables
                            ds_tmp.coords['scenario'] = scen  # add scenario (here ssp) as a coordinate
                            ds_tmp.coords['scenario'].attrs['description'] = 'used scenario (here SSPs)'
                            ds_tmp.coords['bias_correction'] = bc[1:]
                            ds_tmp.coords['basin_idx'] = basin_idx 
                            ds_tmp.coords['basin_name'] = basin 
                            ds_tmp.coords['glaciers_in_basin'] = len(rgis_basin)
                            ds_tmp.coords['glacierised_area_perc'] = 100*area_basin_glacier/area_basin_total
                            ds_tmp = ds_tmp.expand_dims("scenario")  # add SSO as a dimension to all Data variables
                            ds_tmp.attrs['creation_date'] = creation_date  # also add todays date for info
                            ds_tmp.runoff.attrs = {'unit':'kg yr-1', 
                                                   'description':'Annual glacier runoff: sum of annual melt and liquid precipitation on and off the glacier using a fixed-gauge with a glacier minimum reference area from year 2000'}
                            ds_tmp.runoff_monthly.attrs = {'unit':'kg month-1',
                                                           'description':'Monthly glacier runoff from sum of monthly melt and liquid precipitation on and off the glacier using a fixed-gauge with a glacier minimum reference area from year 2000'}
                            ds_all.append(ds_tmp)  # add the dataset with extra coordinates to our final ds_all array
  
                        ds_merged = xr.concat(ds_all, dim='rgi_id')  
                        ds_merged.to_netcdf(f'{path}/basins/{basin_idx}/basin_{basin_idx}_run_hydro_{hist}{bc}{rid}.nc')
        
                    except OSError as err:  # here we land if an error occured
                        if str(err) == 'no files to open':  # This is the error message if the GCM, SCENARIO (here ssp) combination does not exist
                            pass #print(f'No data for gcm {GCM} with scenario {scen} found!')  # print a descriptive message
                        else:
                            raise OSError(err)  # if an other error occured we just raise it
                        # do the actual merging
                        # this creates too large files 
                        #ds_merged = xr.combine_by_coords(ds_all, fill_value=np.nan)  # define how the missing GCM, SCENARIO combinations should be filled  
                        #ds_merged.runoff.attrs = {'unit':'kg yr-1',
                        #             'description':'Annual glacier runoff: sum of annual melt and liquid precipitation on and off the glacier, minimum reference area: 2000'}
                        #ds_merged.runoff_monthly.attrs = {'unit':'kg month-1',
                        #             'description':'Monthly glacier runoff: sum of monthly melt and liquid precipitation on and off the glacier, minimum reference area: 2000'}
                        #ds_merged.to_netcdf(f'{path}/basins/basin_{basin_idx}_combined_run_hydro_{hist}_endyr2100_CMIP6{bc}.nc')

6101
6104
6110
6202
6209
6213
6219
6223
6227
6237
6241
6242
6243
6254
6255


--> an example how to load and plot e.g. the annual runoff for a single basin is given in https://nbviewer.org/urls/cluster.klima.uni-bremen.de/~oggm/oggm-standard-projections/analysis_notebooks/workflow_to_analyse_per_glacier_projection_files.ipynb?flush_cache=true 

**Check if all basins are there**

In [22]:
import os

def count_folders_and_files(directory):
    num_folders = 0
    num_files = 0

    for _, dirs, files in os.walk(directory):
        num_folders += len(dirs)
        num_files += len(files)

    return num_folders, num_files

directory = f'{path}/basins/'
folders, files = count_folders_and_files(directory)

#ssert folders==75
gcm_ssp_combinations = len(gcms_cmip6)/2 # / 2 because pr/tas values
assert files==gcm_ssp_combinations*2*75 # *2 because there are two historical options

def count_files_per_folder(directory):
    folder_counts = {}

    for root, dirs, files in os.walk(directory):
        folder_name = os.path.basename(root)
        folder_counts[folder_name] = len(files)

    return folder_counts

file_counts = count_files_per_folder(directory)

for folder, count in file_counts.items():
    try:
        assert count==int(gcm_ssp_combinations*2) # *2 because there are two historical options
    except:
        print(folder,count)

 0
.ipynb_checkpoints 0
